# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [15]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key

In [16]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("../output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID           City      Lat       Lng  Max Temp  Humidity  Cloudiness  \
0        0       ust-nera  64.5667  143.2000    -32.60        89         100   
1        1    east london -33.0153   27.9116     23.96        87         100   
2        2    west island -12.1568   96.8225     26.99        83          40   
3        3       zharkent  44.1628   80.0000     -7.06        74          64   
4        4  alice springs -23.7000  133.8833     21.23        76          88   

   Wind Speed        Country        Date  
0        0.33       Ust-Nera  1707254186  
1        6.87    East London  1707254187  
2        3.60    West Island  1707254187  
3        2.04       Zharkent  1707254188  
4        6.69  Alice Springs  1707254188

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [17]:
%%capture --no-display

# Configure the map plot
map_plot = city_data_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 800,
    frame_height = 700,
    color = "Country",
    size = "Humidity"
)

# Display the map
map_plot

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Points.I :Points   [Lng,Lat]   (Country,Humidity)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [4]:
# Narrow down cities that fit criteria and drop any results with null values
no_clouds_df = city_data_df.loc[city_data_df["Cloudiness"] == 0]
# Drop any rows with null values
no_clouds_df = no_clouds_df.dropna()

# Display sample data
no_clouds_df.head()

City_ID            City      Lat       Lng  Max Temp  Humidity  \
8         8         kyaukse  21.6000   96.1333     69.01        43   
28       28        ardestan  33.3761   52.3694     45.34        40   
37       37  margaret river -33.9500  115.0667     59.99        68   
39       39          kodiak  57.7900 -152.4072     22.51        93   
42       42      marshfield  44.6689  -90.1718     49.55        53   

    Cloudiness  Wind Speed            Country        Date  
8            0        3.83            Kyaukse  1707244837  
28           0        7.92           Ardestān  1707244844  
37           0       11.79     Margaret River  1707244631  
39           0        0.00  Saint Paul Harbor  1707244848  
42           0        8.05         Marshfield  1707244848

### Step 3: Create a new DataFrame called `hotel_df`.

In [5]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
hotel_df = city_data_df[['City', 'Country', 'Lat', 'Lng', 'Humidity']].copy()
# Add an empty column, "Hotel Name," to the DataFrame so you can store the hotel found using the Geoapify API
hotel_df['Hotel Name'] = ""
# Display sample data
hotel_df.head()

City        Country      Lat       Lng  Humidity Hotel Name
0  blackmans bay  Blackmans Bay -43.0167  147.3167        80           
1       kingston       Kingston  17.9970  -76.7936        53           
2       bilibino       Bilibino  68.0546  166.4372       100           
3          heihe          Heihe  50.2441  127.4902        95           
4         badger         Badger  64.8000 -147.5333        82

### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [8]:
# Set parameters to search for a hotel
radius = 10000
params = {
    "apiKey": geoapify_key,
    "categories": "accommodation.hotel",
    "limit": 20

}

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    lat = row["Lat"]
    lng = row["Lng"]
    
    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary /// access GEOAPify
    params["filter"] = f"circle:{lng},{lat},{radius}"
    params["bias"] = f"proximity:{lng},{lat}"
    
    # Set base URL
    base_url = "https://api.geoapify.com/v2/places"


    # Make and API request using the params dictionaty
    name_address = requests.get(base_url, params=params)
    
    # Convert the API response to JSON format
    name_address = name_address.json()
    print(name_address)
    # Grab the first hotel from the results and store the name in the hotel_df DataFrame
    try:
        hotel_df.loc[index, "Hotel Name"] = name_address["features"][0]["properties"]["name"]
    except (KeyError, IndexError):
        # If no hotel is found, set the hotel name as "No hotel found".
        hotel_df.loc[index, "Hotel Name"] = "No hotel found"
        
    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'Hotel Name']}")

# Display sample data
hotel_df

Starting hotel search
{'type': 'FeatureCollection', 'features': [{'type': 'Feature', 'properties': {'name': 'Villa Howden', 'country': 'Australia', 'country_code': 'au', 'state': 'Tasmania', 'city': 'Hobart', 'village': 'Howden', 'municipality': 'Kingborough', 'postcode': '7055', 'street': 'Howden Road', 'lon': 147.27947946462487, 'lat': -43.0097946, 'state_code': 'TAS', 'formatted': 'Villa Howden, Howden Road, Hobart TAS 7055, Australia', 'address_line1': 'Villa Howden', 'address_line2': 'Howden Road, Hobart TAS 7055, Australia', 'categories': ['accommodation', 'accommodation.hotel', 'building', 'building.accommodation'], 'details': [], 'datasource': {'sourcename': 'openstreetmap', 'attribution': '© OpenStreetMap contributors', 'license': 'Open Database Licence', 'url': 'https://www.openstreetmap.org/copyright', 'raw': {'name': 'Villa Howden', 'osm_id': 618783944, 'tourism': 'hotel', 'building': 'yes', 'osm_type': 'w'}}, 'distance': 3112, 'place_id': '51af39ecc5f168624059c246850841814

City          Country      Lat       Lng  Humidity  \
0      blackmans bay    Blackmans Bay -43.0167  147.3167        80   
1           kingston         Kingston  17.9970  -76.7936        53   
2           bilibino         Bilibino  68.0546  166.4372       100   
3              heihe            Heihe  50.2441  127.4902        95   
4             badger           Badger  64.8000 -147.5333        82   
..               ...              ...      ...       ...       ...   
577            khash            Khāsh  28.2211   61.2158        39   
578  kamennomostskiy  Kamennomostskiy  44.2983   40.1856        86   
579         galliano         Galliano  29.4422  -90.2992        54   
580       lagunillas       Lagunillas  10.1301  -71.2595        69   
581             kulp             Kulp  38.4972   41.0122        98   

                                            Hotel Name  
0                                         Villa Howden  
1                                      Aphrodite Hotel  
2                                       No hotel found  
3                                      Санкт-Петербург  
4                                     Hotel North Pole  
..                                                 ...  
577                                     No hotel found  
578                                  Усадьба Парфёнова  
579  Fairfield Inn & Suites by Marriott Cut Off-Gal...  
580                                      Palacio Suite  
581                                     No hotel found  

[582 rows x 6 columns]

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [14]:
%%capture --no-display

# Configure the map plot
map_plot2 = hotel_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 800,
    frame_height = 700,
    color = "Country",
    hover_cols = ["Hotel Name","Country"]
)

# Display the map
map_plot2

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Points.I :Points   [Lng,Lat]   (Country,Hotel Name)